In [ ]:
#@title Update Plotly & VEGAS to latest version
!pip install -U plotly
!pip install -U "altair[all]"

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.7/213.7 kB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 198.6/198.6 kB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.5/54.5 kB 2.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 658.1/658.1 kB 14.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 25.1/25.1 MB 16.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.1/30.1 MB 13.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 727.4/727.4 kB 11.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 13.3 MB/s eta 0:00:00
  Attempting uninstall: altair
    Found existing installation: altair 4.2.2
    Uninstalling altair-4.2.2:
      Successfully uninstalled altair-4.2.2


In [ ]:
%%capture

!rm *.csv*

#@title Download Scrapped Data from Inteli.Gente
!wget "https://github.com/Rafaelsoz/Pratica-Ciencia-Dados-II/raw/main/datasets/Dimens%C3%B5es/Econ%C3%B4mica.csv"
!wget "https://github.com/Rafaelsoz/Pratica-Ciencia-Dados-II/raw/main/datasets/Dimens%C3%B5es/Capacidades%20Institucionais.csv"
!wget "https://github.com/Rafaelsoz/Pratica-Ciencia-Dados-II/raw/main/datasets/Dimens%C3%B5es/Meio%20Ambiente.csv"
!wget "https://github.com/Rafaelsoz/Pratica-Ciencia-Dados-II/raw/main/datasets/Dimens%C3%B5es/Sociocultural.csv"

In [ ]:
import numpy as np
import pandas as pd
import altair as alt

import seaborn as sns
import matplotlib.colors as mcolors
from matplotlib import pyplot as plt

import zlib
from scipy import optimize
from scipy.stats import entropy
from scipy.interpolate import InterpolatedUnivariateSpline

from tqdm.notebook import tqdm

sns.set_style("darkgrid")

In [ ]:
# Load data
ECO = pd.read_csv("Econômica.csv").iloc[:, 1:]
CI = pd.read_csv("Capacidades Institucionais.csv").iloc[:, 1:]
MA = pd.read_csv("Meio Ambiente.csv").iloc[:, 1:]
SC = pd.read_csv("Sociocultural.csv").iloc[:, 1:]

# Target variable
level = ECO['Nivel']

In [ ]:
#@markdown Percebemos que todas as dimensões possuem valores nulos (NaNs) em várias cidades. Isso acontece por que a plataforma Inteli.Gente não encontrou dados sobre aquele atributo para aquele município. Na análise da plataforma, os valores nulos são considerados 0, então vamos substituir todos os valores nulos por zero nos dados.
ECO = ECO.fillna(0)
CI = CI.fillna(0)
MA = MA.fillna(0)
SC = SC.fillna(0)

In [ ]:
#@title Seleciona Apenas Colunas Numéricas e Remove Colunas com Valores Constantes

# Converte "Coleta seletiva de resíduos no município" de booleano para inteiro
ECO["Coleta seletiva de resíduos no município"] = ECO["Coleta seletiva de resíduos no município"].astype("int64")

# Select only numerical values
ECO = ECO[ECO.columns[(ECO.dtypes == "float64") | (ECO.dtypes == "int64")]]
CI = CI[CI.columns[(CI.dtypes == "float64") | (CI.dtypes == "int64")]]
MA = MA[MA.columns[(MA.dtypes == "float64") | (MA.dtypes == "int64")]]
SC = SC[SC.columns[(SC.dtypes == "float64") | (SC.dtypes == "int64")]]


# Remove 'Codigo', 'Nome' & 'Nivel'
ECO = ECO.iloc[:, 2:]
CI = CI.iloc[:, 2:]
MA = MA.iloc[:, 2:]
SC = SC.iloc[:, 2:]

# Remove constant valued columns
ECO = ECO[ECO.columns[ECO.nunique() > 1]]
CI = CI[CI.columns[CI.nunique() > 1]]
MA = MA[MA.columns[MA.nunique() > 1]]
SC = SC[SC.columns[SC.nunique() > 1]]

In [ ]:
#@title Multi Scatter Plot 1-D
import pandas as pd
import plotly.graph_objects as go

def multi_scatter_1d(df: pd.DataFrame,
                     target: pd.Series,
                     colormap: str = "Bluered"):

  """
  Generates a normalized one-dimensional scatterplot for each column in the DataFrame.

  Parameters
  ----------
  df : pd.DataFrame
      A multi-dimensional DataFrame containing the data to be plotted.

  target : pd.Series
      The target data, either discrete or continuous, used to colorize the scatterplot.

  colormap: str
      Colormap name to be used when setting the color scale.
  """

  # Apply normalization to data to be inside [0, 1] range
  data = (df - df.min()) / (df.max() - df.min())

  # Array to store the plot data
  values = []

  for idx, column in enumerate(data.columns):

    # Get the unique values and its frequency
    row, indices, counts = np.unique(data.iloc[:, idx], return_counts=True, return_index=True)

    # Sort the target values by the unique values order
    target_data = target[indices]

    # Add the index of each column to it's name
    column_text = f"({idx}) {column}"

    # Create a DataFrame with metadata for the current column
    row = pd.DataFrame(zip([column_text] * row.size, row, counts, target_data),
                      columns=["column", "value", "count", "target"])

    # Set the point colors with the most frequent target value
    row["color"] = row["value"].apply(lambda x: target[data[column] == x].mode()).iloc[:, 0]

    # Append current column to values array
    values.append(row)

  # Concatenate all columns
  values = pd.concat(values)

  fig = go.Figure(
    go.Scatter(
      x=values["column"],
      y=values["value"],
      mode='markers',
      marker=dict(
          size=values["count"].apply(lambda x: x ** (1/10)) * 10,
          color=values["color"],
          showscale=True,
          colorscale=colormap,
          line=dict(width=0),
          colorbar=dict(title=dict(text="Escala do Valor Alvo", side="right"))
      ),
      text=values["color"].apply(lambda x: f"Valor Alvo: {x}")
    )
  )

  fig.update_layout(
    title=dict(
      text="Distribuição dos Valores",
      subtitle=dict(
          text=f"Distribuição dos Valores de Cada Coluna do DataFrame ({df.shape[1]} Colunas)",
          font=dict(color="gray", size=13),
      ),
    ),
    xaxis_title="Colunas",
    yaxis_title="Valores Normalizados",
    template="plotly_white",
    margin = dict(t=60, b=40, l=40, r=20), # top, bottom, left, right
    width=1000,
    height=500,
  )

  fig.update_xaxes(showticklabels=False)

  fig.show()

In [ ]:
#@title Compute Meta-Features
# data = (ECO - ECO.min()) / (ECO.max() - ECO.min())
# target = level

def compute_metafeatures(data: pd.DataFrame,
                         target: pd.Series):

  # Apply normalization to data to be inside [0, 1] range
  data = (data - data.min()) / (data.max() - data.min())

  # Array to store the plot data
  values = []

  for idx, column in enumerate(data.columns):

    # Get the unique values and its frequency
    row, indices, counts = np.unique(data.iloc[:, idx], return_counts=True, return_index=True)

    # Sort the target values by the unique values order
    target_data = target[indices]

    # Add the index of each column to it's name
    # column_text = f"({idx}) {column}"
    column_text = column

    # Create a DataFrame with metadata for the current column
    row = pd.DataFrame(zip([column_text] * row.size, row, counts, target_data),
                      columns=["column", "value", "count", "target"])

    # Set the point colors with the most frequent target value
    row["color"] = row["value"].apply(lambda x: target[data[column] == x].mode()).iloc[:, 0]

    # Append current column to values array
    values.append(row)

  # Concatenate all columns
  values = pd.concat(values)

  nunique = data.nunique()

  mean_value = data.mean()
  median_value = data.median()
  dist_shift = mean_value - median_value

  mean_size = (data.count() - data.nunique()) / data.nunique()

  max_target = values.groupby(by='column')[['value', 'target']].apply(lambda x: x.iloc[x['value'].argmax()]['target'])
  min_target = values.groupby(by='column')[['value', 'target']].apply(lambda x: x.iloc[x['value'].argmin()]['target'])

  q25 = data.quantile(0.25)
  q50 = data.quantile(0.50)
  q75 = data.quantile(0.75)

  return nunique, mean_value, median_value, dist_shift, mean_size, max_target, min_target, q25, q50, q75

In [ ]:
#@title Função para Organizar Colunas Seguindo o Método 3
from sklearn.cluster import KMeans
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import silhouette_score, make_scorer

from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler

import warnings

def sort_columns_kmeans(metafeatures: pd.DataFrame):

  X = metafeatures

  kmeans = Pipeline([
    ('Padronização', StandardScaler()),
    ('KMeans', KMeans(n_clusters=2, random_state=0, n_init="auto")),
  ])


  with warnings.catch_warnings():
      warnings.simplefilter("ignore")

      clf = GridSearchCV(estimator=kmeans,
                        param_grid={'KMeans__n_clusters': np.arange(2, 10, 1)},
                        scoring=make_scorer(silhouette_score)).fit(X, X)

  n_clusters = clf.best_params_['KMeans__n_clusters']

  labels = Pipeline([
    ('Padronização', StandardScaler()),
    ('KMeans', KMeans(n_clusters=n_clusters, random_state=0, n_init="auto")),
  ]).fit(X)['KMeans'].labels_

  columns_order = pd.DataFrame(labels, index=X.index, columns=['Kmeans']).sort_values(by='Kmeans').index

  return columns_order

In [ ]:
#@title Calculando Influência da Proporção de Valores Únicos no Vetor no Fator de Aleatoriedade
def create_vector(n: int = 100, u: float = 0.5):

    # Calcula o número de valores unicos do vetor
    u = int(n * u)

    # Gera u valores únicos
    unique_values = np.random.choice(range(1, u + 1), u, replace=False)

    # Repete esses valores para preencher o vetor de tamanho n
    vector = np.random.choice(unique_values, n, replace=True)

    return vector

def r(x, zx):
  return 1 - (x - zx) / x

def compute_r(A: np.array):
    x = A.size * A.itemsize
    zx = len(zlib.compress(A))

    return r(x, zx)

runs = {}

for n in tqdm([100, 500, 1000]):

  uvalues = np.linspace(0.01, 1, n)
  rvalues = np.array([compute_r(create_vector(n, u)) for u in uvalues])

  runs[n] = (uvalues, rvalues)

# Correção do víes do Fator de Aleatoriedade
f = InterpolatedUnivariateSpline(x=runs[100][0], y=runs[100][1])
f.set_smoothing_factor(0.0)

  0%|          | 0/3 [00:00<?, ?it/s]

In [ ]:
#@markdown A porcentagem de valores únicos no vetor de entrada possui influência sob o valor final do fator de aleatoriedade. Isso causa problemas ao compararmos variáveis que possuem quantidades de valores únicos diferentes.

#@markdown Para remover esse víes da análise, ajustei uma função ao comportamento de $r(x, Z(x))$ em função do número de valores únicos em $x$, e defini os resíduos como: $r(x, Z(x)) - f(u)$, sendo $u$ a proporção de valores únicos no vetor de entrada.

import plotly.graph_objects as go

fig = go.Figure(
	[go.Scatter(
		x=runs[run][0],
		y=runs[run][1],
    name=run
	) for run in runs.keys()] +
  [
    go.Scatter(
        x=runs[run][0],
        y=runs[run][1] - f(runs[run][0]),
        name=f"Resíduos (n={run})"
    ) for run in runs.keys()]
)

fig.update_layout(
	title="Comportamento de r(x, zx) em Função do Número de Valores Únicos",
	xaxis_title="Porcentagem de Valores Únicos no Vetor",
	yaxis_title="Fator de Aleatoriedade",
	template="plotly_white",
	margin = dict(t=60, b=20, l=20, r=20), # top, bottom, left, right
	width=800,
	height=400,
  xaxis=dict(tickformat=',.0%', range=[0, 1])
)

# Adiciona linhas nos eixos da figura
fig.update_xaxes(showline=True, linewidth=.5, linecolor='grey')
fig.update_yaxes(showline=True, linewidth=.5, linecolor='grey')

fig.show()

In [ ]:
#@title Funções para Calcular Aleatoriedade de um Vetor

def r_hat(x: int,
          zx: int,
          u: float) -> float:

  """
  Calcula o Fator de Aleatoriedade Corrigido

  Parametros
  ----------
  x: int
    Tamanho do Vetor em Bytes

  zx: int
    Tamanho do Vetor Comprimido em Bytes

  u: float
    Porcentagem de Valores Únicos no Vetor

  Retorna
  -------
  float:
    Fator de Aleatoriedade Corrigido
  """

  return 1 - (x - zx) / x - f(u)


def compute_randomness(vector: np.array) -> float:

  # Tamanho do Vetor em Bytes
  x = vector.size * vector.itemsize

  # Tamanho do Vetor Comprimido em Bytes
  zx = len(zlib.compress(vector))

  # Porcentagem de Valores Únicos no Vetor
  u = np.unique(vector).size / vector.size

  # Fator de Aleatoriedade Corrigido
  return r_hat(x, zx, u), (x, zx, u)


def compute_entropy(vector: np.array,
                    target: np.array = None,
                    bins: int = 1000) -> float:

  """
  Calcula a Entropia de Shannon de um Vetor

  Parametros
  ----------
  vector: np.array
    Vetor para calcular a entropia

  target: np.array
    Vetor Alvo para calcular a Divergência de KL. Padrão: None

  bins: int
    Número de Bins para utilizar no calculo do Histograma. Padrão: 1000

  Retorna
  -------
  float:
    Entropia de Shannon ou Divergência de KL dos vetores  de entrada.
  """

  # Compute the histogram bin counts from vector values
  hist, _ = np.histogram(vector, bins=bins)

  if target is not None:
    target_hist, _ = np.histogram(target, bins=bins)
    return entropy(hist, target_hist + 1)

  # Compute the Shannon entropy from histogram bin counts
  return entropy(hist)


# Dimensão Econômica

In [ ]:
#@title Define o DataFrame para Utilizar na Análise
df = ECO

In [ ]:
#@title Relações entre os Atributos
metafeatures = compute_metafeatures(df, level)
X = pd.concat(metafeatures, axis=1)

columns_order = sort_columns_kmeans(metafeatures=X)

multi_scatter_1d(df[columns_order], level)

In [ ]:
#@title Calcular Métricas de Aleatoriedade para as Colunas do DataFrame
metrics = []

for idx, column in enumerate(columns_order):
  A = df.loc[:, column].to_numpy()

  # Fator de Aleatoriedade Corrigido do Vetor
  r_h, (x, zx, u) = compute_randomness(A)

  # Entropia de Shannon do Vetor
  e = compute_entropy(A)

  # Divergência de KL entre Vetor e Vetor-Alvo
  k = compute_entropy(A, level)

  metrics.append((f"({idx}) {column}", column, x, zx, u, r_h, e, k))

metrics = pd.DataFrame(metrics, columns=['Nome', 'Coluna', 'Tamanho (bytes)', 'Tamanho Zip (Bytes)',
                                         '% Valores Unicos', 'Aleatoriedade (r)', 'Entropia', 'KL'])

metrics.loc[metrics['Aleatoriedade (r)'] < 0, "Aleatoriedade (r)"] = 0

metrics.head(5)

Nome  \
0                 (0) Números de estações rádio base   
1  (1) Escala de acesso a banda larga fixa de alt...   
2           (2) Escala de acesso a banda larga móvel   
3  (3) Percentual de domicílios com população viv...   
4            (4) Escala de acesso a banda larga fixa   

                                              Coluna  Tamanho (bytes)  \
0                     Números de estações rádio base            44560   
1  Escala de acesso a banda larga fixa de alta ve...            44560   
2               Escala de acesso a banda larga móvel            44560   
3  Percentual de domicílios com população vivendo...            44560   
4                Escala de acesso a banda larga fixa            44560   

   Tamanho Zip (Bytes)  % Valores Unicos  Aleatoriedade (r)  Entropia  \
0                 8657          0.046140           0.071553  4.853287   
1                42182          0.998923           0.699056  5.859058   
2                16256          0.756194           0.125889  5.645718   
3                 3784          0.105027           0.000000  1.074158   
4                15058          0.504668           0.119457  5.590590   

         KL  
0  3.922450  
1  2.827369  
2  3.096736  
3  3.344354  
4  3.182721

In [ ]:
#@title Relação entre Entropia de Shannon e Fator de Aleatoriedade

# Calcula a correlação entre Fator de Aleatoriedade e Entropia
corr = metrics[['Aleatoriedade (r)', 'Entropia']].corr(method="spearman").iloc[0,1]

# Limites do retângulo
x_min, x_max = 0, 0.18
y_min, y_max = 0, 3

# Adiciona uma coluna para indicar se o ponto está dentro do retângulo
metrics['Comportamento'] = metrics.apply(
    lambda row: 'Bem Comportado' if (x_min <= row['Aleatoriedade (r)'] <= x_max and y_min <= row['Entropia'] <= y_max) else 'Mal Comportado',
    axis=1
)

# Calcula o Score de Aleatoriedade dos Atributos (Média entre Entropia e Fator de Aleatoriedade)
metrics['Score'] = (metrics['Aleatoriedade (r)'] + metrics['Entropia']) / 2

points = alt.Chart(metrics).mark_point().encode(
    x=alt.X("Aleatoriedade (r)", title="Fator de Aleatoriedade"),
    y=alt.Y("Entropia", title="Entropia de Shannon"),
    color=alt.Color("Comportamento:N",
                    scale=alt.Scale(domain=['Bem Comportado', 'Mal Comportado'], range=['blue', 'red']),
                    legend=alt.Legend(title="Comportamento do Atributo")),
    tooltip=[
        alt.Tooltip("Nome", title="Coluna"),
        alt.Tooltip("Aleatoriedade (r)", title="Fator de Aleatoriedade", format=".3f"),
        alt.Tooltip("Entropia", title="Entropia de Shannon", format=".3f"),
        alt.Tooltip("Score", title="Score de Aleatoriedade", format=".3f"),
    ]
)

rect = alt.Chart(pd.DataFrame({
    'x': [x_max], 'x2': [x_min],
    'y': [y_max], 'y2': [y_min]
})).mark_rect(opacity=0.3).encode(
    x='x:Q', x2='x2:Q',
    y='y:Q', y2='y2:Q',
    color=alt.value("grey")
)

good_zone = metrics[metrics['Comportamento'] == "Bem Comportado"]

good_points = alt.Chart(good_zone).mark_point().encode(
    x=alt.X("Aleatoriedade (r)", title="Fator de Aleatoriedade"),
    y=alt.Y("Entropia", title=""),
    color=alt.Color("Comportamento:N",
                    scale=alt.Scale(domain=['Bem Comportado', 'Mal Comportado'], range=['blue', 'red']),
                    legend=alt.Legend(title="Comportamento do Atributo")),
    tooltip=[
        alt.Tooltip("Nome", title="Coluna"),
        alt.Tooltip("Aleatoriedade (r)", title="Fator de Aleatoriedade", format=".3f"),
        alt.Tooltip("Entropia", title="Entropia de Shannon", format=".3f"),
        alt.Tooltip("Score", title="Score de Aleatoriedade", format=".3f"),
    ]
).properties(
    title=alt.Title(
        text="Atributos Dentro da Zona Bem Comportada",
        subtitle=f"Existem {good_zone.shape[0]} atributos bem comportados nessa zona",
        anchor="start",     # Alinha o título ao início (canto esquerdo)
        align="left",       # Alinha o texto à esquerda
    ),
)

plot = (rect + points).properties(
    title=alt.Title(
        text="Relação entre Entropia de Shannon e Fator de Aleatoriedade",
        subtitle=f"A Correlação de Spearman entre o Fator de Aleatoriedade e a Entropia de Shannon é de {corr:.4f}",
        anchor="start",     # Alinha o título ao início (canto esquerdo)
        align="left",       # Alinha o texto à esquerda
    ),
    width=500,
    height=300,
)

(plot | good_points).properties(
    padding={"left": 25, "right": 25, "top": 25, "bottom": 25}  # Adiciona padding externo
).interactive()

alt.HConcatChart(...)

In [ ]:
#@title Análise dos Atributos Bem Comportados
good_columns = metrics[metrics['Comportamento'] == "Bem Comportado"]['Coluna'].tolist()

# Define o DataFrame com apenas os atributos comportados
df2 = df[good_columns].copy()

metafeatures = compute_metafeatures(df2, level)
X = pd.concat(metafeatures, axis=1)

columns_order_hat = sort_columns_kmeans(metafeatures=X)

multi_scatter_1d(df2[columns_order_hat], level)

In [ ]:
#@title Correlograma dos Atributos Bem Comportados

# Filtra apenas os valores do triângulo inferior sem a diagonal principal
corr = df2.corr()
corr = corr.where(np.tril(np.ones(corr.shape), k=0).astype(bool))

# Calcula a matriz de correlação
corr_matrix = corr.reset_index().melt(id_vars='index', var_name='Variable2', value_name='Correlation')

# Renomeia a coluna 'index' para 'Variable1' para melhor compreensão
corr_matrix = corr_matrix.rename(columns={'index': 'Variable1'})

corr_matrix = corr_matrix.dropna()

# Adicionar métricas de aleatoriedade
corr_matrix = corr_matrix.merge(metrics, left_on="Variable1", right_on="Coluna", how="inner")
corr_matrix = corr_matrix.merge(metrics, left_on="Variable2", right_on="Coluna", how="inner")

base = alt.Chart(corr_matrix).encode(
    x=alt.X("Variable2:N", sort=corr.columns, title=""),
    y=alt.Y("Variable1:N", sort=corr.columns, title=""),
    color=alt.Color("Correlation:Q", scale=alt.Scale(scheme='spectral', domain=(-1, 1))),
    tooltip=[
        alt.Tooltip('Variable1:N', title='Atributo 1'),
        alt.Tooltip('Variable2:N', title='Atributo 2'),
        alt.Tooltip('Correlation:Q', title='Correlação de Pearson', format='.2f'),

        alt.Tooltip('Aleatoriedade (r)_x:Q', title="Fator de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Aleatoriedade (r)_y:Q', title="Fator de Aleatoriedade (2)", format='.3f'),

        alt.Tooltip('Entropia_x:Q', title="Entropia de Shannon (1)", format='.3f'),
        alt.Tooltip('Entropia_y:Q', title="Entropia de Shannon (2)", format='.3f'),

        alt.Tooltip('Score_x:Q', title="Score de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Score_y:Q', title="Score de Aleatoriedade (2)", format='.3f'),
    ]
)

corr = base.mark_rect()

text = base.mark_text(baseline="middle").encode(
    text=alt.Text("Correlation:Q", format='.2f'),
    color=alt.value("white")
)

(corr + text).properties(
    title=alt.Title(
        text="Correlograma entre os atributos considerados 'Bem-Comportados'",
        subtitle=f"Atualmente existem {df2.shape[1]} atributos na análise"
    ),
    width=700,
    height=300
)

alt.LayerChart(...)

In [ ]:
#@title Seleção de Atributos pela Correlação e pelo Score de Aleatoriedade
metadata = corr_matrix[['Variable1', 'Variable2', 'Score_x', 'Score_y', 'Correlation']]

# Remove pares com a mesma variável
metadata = metadata[metadata.eval("Variable1 != Variable2")]

features = metadata['Variable1'].unique()

best_features = []

for feature in features:
  d = metadata[metadata['Variable1'] == feature]

  # Procura atributos altamente correlacionados com o atributo atual
  d = d[d['Correlation'] > 0.7]

  if d.shape[0] == 0:
    # Caso não houver nenhum atributo
    # correlacionado com o atributo atual, seleciona ele.
    best_features.append(feature)

  if d.shape[0] > 1:
    # Caso houver outros atributos altamente
    # correlacionados com o atual, escolhe o menos aleatório

    # Procura o nome e score da variável
    # correlacionada com menor score de aleatoriedade
    var_name, var_score = d.loc[d['Score_y'].idxmin(), ['Variable2', 'Score_y']].tolist()

    # Procura o score de aleatoriedade da variável atual
    current_score = d['Score_x'].min()

    # Seleciona a variável menos aleatória
    if current_score <= var_score:
      best_features.append(feature)
    else:
      best_features.append(var_name)


In [ ]:
#@title Correlograma dos Atributos Bem Comportados e Pouco Correlacionados

# Define o DataFrame com Atributos Comportados e Poucos Correlacionados
df3 = df2[list(set(best_features))]

# Filtra apenas os valores do triângulo inferior sem a diagonal principal
corr = df3.corr()
corr = corr.where(np.tril(np.ones(corr.shape), k=0).astype(bool))

# Calcula a matriz de correlação
corr_matrix = corr.reset_index().melt(id_vars='index', var_name='Variable2', value_name='Correlation')

# Renomeia a coluna 'index' para 'Variable1' para melhor compreensão
corr_matrix = corr_matrix.rename(columns={'index': 'Variable1'})

corr_matrix = corr_matrix.dropna()

# Adicionar métricas de aleatoriedade
corr_matrix = corr_matrix.merge(metrics, left_on="Variable1", right_on="Coluna", how="inner")
corr_matrix = corr_matrix.merge(metrics, left_on="Variable2", right_on="Coluna", how="inner")

base = alt.Chart(corr_matrix).encode(
    x=alt.X("Variable2:N", sort=corr.columns, title=""),
    y=alt.Y("Variable1:N", sort=corr.columns, title=""),
    color=alt.Color("Correlation:Q", scale=alt.Scale(scheme='spectral', domain=(-1, 1))),
    tooltip=[
        alt.Tooltip('Variable1:N', title='Atributo 1'),
        alt.Tooltip('Variable2:N', title='Atributo 2'),
        alt.Tooltip('Correlation:Q', title='Correlação de Pearson', format='.2f'),

        alt.Tooltip('Aleatoriedade (r)_x:Q', title="Fator de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Aleatoriedade (r)_y:Q', title="Fator de Aleatoriedade (2)", format='.3f'),

        alt.Tooltip('Entropia_x:Q', title="Entropia de Shannon (1)", format='.3f'),
        alt.Tooltip('Entropia_y:Q', title="Entropia de Shannon (2)", format='.3f'),

        alt.Tooltip('Score_x:Q', title="Score de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Score_y:Q', title="Score de Aleatoriedade (2)", format='.3f'),
    ]
)

corr = base.mark_rect()

text = base.mark_text(baseline="middle").encode(
    text=alt.Text("Correlation:Q", format='.2f'),
    color=alt.value("white")
)

(corr + text).properties(
    title=alt.Title(
        text="Correlograma entre os atributos considerados 'Bem-Comportados' e Pouco Correlacionados",
        subtitle=f"Atualmente existem {df3.shape[1]} atributos na análise"
    ),    width=700,
    height=300
)

alt.LayerChart(...)

In [ ]:
#@title Modelo de Regressão Linear Ajustada a Cada Dataset
from sklearn.linear_model import LinearRegression

y = level.copy()

results = [
    {"Dataset": "Original", "Variáveis": df.shape[1], "R2": LinearRegression().fit(df, y).score(df, y)},
    {"Dataset": "Bem Comportados",  "Variáveis": df2.shape[1],"R2": LinearRegression().fit(df2, y).score(df2, y)},
    {"Dataset": "Bem Comportados e Pouco Correlacionados", "Variáveis": df3.shape[1],"R2": LinearRegression().fit(df3, y).score(df3, y)}
]

pd.DataFrame(results)

Dataset  Variáveis        R2
0                                 Original         29  0.833337
1                          Bem Comportados         20  0.659526
2  Bem Comportados e Pouco Correlacionados         18  0.658444

# Dimensão Capacidades Institucionais

In [ ]:
#@title Define o DataFrame para Utilizar na Análise
df = CI

In [ ]:
#@title Relações entre os Atributos
metafeatures = compute_metafeatures(df, level)
X = pd.concat(metafeatures, axis=1)

columns_order = sort_columns_kmeans(metafeatures=X)

multi_scatter_1d(df[columns_order], level)

In [ ]:
#@title Calcular Métricas de Aleatoriedade para as Colunas do DataFrame
metrics = []

for idx, column in enumerate(columns_order):
  A = df.loc[:, column].to_numpy()

  # Fator de Aleatoriedade Corrigido do Vetor
  r_h, (x, zx, u) = compute_randomness(A)

  # Entropia de Shannon do Vetor
  e = compute_entropy(A)

  # Divergência de KL entre Vetor e Vetor-Alvo
  k = compute_entropy(A, level)

  metrics.append((f"({idx}) {column}", column, x, zx, u, r_h, e, k))

metrics = pd.DataFrame(metrics, columns=['Nome', 'Coluna', 'Tamanho (bytes)', 'Tamanho Zip (Bytes)',
                                         '% Valores Unicos', 'Aleatoriedade (r)', 'Entropia', 'KL'])

metrics.loc[metrics['Aleatoriedade (r)'] < 0, "Aleatoriedade (r)"] = 0

metrics.head(5)

Nome  \
0                      (0) Serviços Públicos On-line   
1               (1) Solicitação de Serviços Públicos   
2  (2) Transparência - Execução Orçamentária e Fi...   
3     (3) Transparência dos Dados - Disponibilização   
4         (4) Governança Colaborativa - Responsáveis   

                                              Coluna  Tamanho (bytes)  \
0                          Serviços Públicos On-line            44560   
1                   Solicitação de Serviços Públicos            44560   
2  Transparência - Execução Orçamentária e Financ...            44560   
3         Transparência dos Dados - Disponibilização            44560   
4             Governança Colaborativa - Responsáveis            44560   

   Tamanho Zip (Bytes)  % Valores Unicos  Aleatoriedade (r)  Entropia  \
0                 4844          0.003411           0.142640  2.671974   
1                 3675          0.001975           0.132429  1.903706   
2                 1647          0.001077           0.097635  0.698844   
3                 2750          0.001975           0.111671  1.278135   
4                  183          0.001436           0.060427  0.040994   

         KL  
0  5.216295  
1  5.204414  
2  5.587359  
3  7.206416  
4  3.743030

In [ ]:
#@title Relação entre Entropia de Shannon e Fator de Aleatoriedade

# Calcula a correlação entre Fator de Aleatoriedade e Entropia
corr = metrics[['Aleatoriedade (r)', 'Entropia']].corr(method="spearman").iloc[0,1]

# Limites do retângulo
x_min, x_max = 0, 0.18
y_min, y_max = 0, 3

# Adiciona uma coluna para indicar se o ponto está dentro do retângulo
metrics['Comportamento'] = metrics.apply(
    lambda row: 'Bem Comportado' if (x_min <= row['Aleatoriedade (r)'] <= x_max and y_min <= row['Entropia'] <= y_max) else 'Mal Comportado',
    axis=1
)

# Calcula o Score de Aleatoriedade dos Atributos (Média entre Entropia e Fator de Aleatoriedade)
metrics['Score'] = (metrics['Aleatoriedade (r)'] + metrics['Entropia']) / 2

points = alt.Chart(metrics).mark_point().encode(
    x=alt.X("Aleatoriedade (r)", title="Fator de Aleatoriedade"),
    y=alt.Y("Entropia", title="Entropia de Shannon"),
    color=alt.Color("Comportamento:N",
                    scale=alt.Scale(domain=['Bem Comportado', 'Mal Comportado'], range=['blue', 'red']),
                    legend=alt.Legend(title="Comportamento do Atributo")),
    tooltip=[
        alt.Tooltip("Nome", title="Coluna"),
        alt.Tooltip("Aleatoriedade (r)", title="Fator de Aleatoriedade", format=".3f"),
        alt.Tooltip("Entropia", title="Entropia de Shannon", format=".3f"),
        alt.Tooltip("Score", title="Score de Aleatoriedade", format=".3f"),
    ]
)

rect = alt.Chart(pd.DataFrame({
    'x': [x_max], 'x2': [x_min],
    'y': [y_max], 'y2': [y_min]
})).mark_rect(opacity=0.3).encode(
    x='x:Q', x2='x2:Q',
    y='y:Q', y2='y2:Q',
    color=alt.value("grey")
)

good_zone = metrics[metrics['Comportamento'] == "Bem Comportado"]

good_points = alt.Chart(good_zone).mark_point().encode(
    x=alt.X("Aleatoriedade (r)", title="Fator de Aleatoriedade"),
    y=alt.Y("Entropia", title=""),
    color=alt.Color("Comportamento:N",
                    scale=alt.Scale(domain=['Bem Comportado', 'Mal Comportado'], range=['blue', 'red']),
                    legend=alt.Legend(title="Comportamento do Atributo")),
    tooltip=[
        alt.Tooltip("Nome", title="Coluna"),
        alt.Tooltip("Aleatoriedade (r)", title="Fator de Aleatoriedade", format=".3f"),
        alt.Tooltip("Entropia", title="Entropia de Shannon", format=".3f"),
        alt.Tooltip("Score", title="Score de Aleatoriedade", format=".3f"),
    ]
).properties(
    title=alt.Title(
        text="Atributos Dentro da Zona Bem Comportada",
        subtitle=f"Existem {good_zone.shape[0]} atributos bem comportados nessa zona",
        anchor="start",     # Alinha o título ao início (canto esquerdo)
        align="left",       # Alinha o texto à esquerda
    ),
)

plot = (rect + points).properties(
    title=alt.Title(
        text="Relação entre Entropia de Shannon e Fator de Aleatoriedade",
        subtitle=f"A Correlação de Spearman entre o Fator de Aleatoriedade e a Entropia de Shannon é de {corr:.4f}",
        anchor="start",     # Alinha o título ao início (canto esquerdo)
        align="left",       # Alinha o texto à esquerda
    ),
    width=500,
    height=300,
)

(plot | good_points).properties(
    padding={"left": 25, "right": 25, "top": 25, "bottom": 25}  # Adiciona padding externo
).interactive()

alt.HConcatChart(...)

In [ ]:
#@title Análise dos Atributos Bem Comportados
good_columns = metrics[metrics['Comportamento'] == "Bem Comportado"]['Coluna'].tolist()

# Define o DataFrame com apenas os atributos comportados
df2 = df[good_columns].copy()

metafeatures = compute_metafeatures(df2, level)
X = pd.concat(metafeatures, axis=1)

columns_order_hat = sort_columns_kmeans(metafeatures=X)

multi_scatter_1d(df2[columns_order_hat], level)

In [ ]:
#@title Correlograma dos Atributos Bem Comportados

# Filtra apenas os valores do triângulo inferior sem a diagonal principal
corr = df2.corr()
corr = corr.where(np.tril(np.ones(corr.shape), k=0).astype(bool))

# Calcula a matriz de correlação
corr_matrix = corr.reset_index().melt(id_vars='index', var_name='Variable2', value_name='Correlation')

# Renomeia a coluna 'index' para 'Variable1' para melhor compreensão
corr_matrix = corr_matrix.rename(columns={'index': 'Variable1'})

corr_matrix = corr_matrix.dropna()

# Adicionar métricas de aleatoriedade
corr_matrix = corr_matrix.merge(metrics, left_on="Variable1", right_on="Coluna", how="inner")
corr_matrix = corr_matrix.merge(metrics, left_on="Variable2", right_on="Coluna", how="inner")

base = alt.Chart(corr_matrix).encode(
    x=alt.X("Variable2:N", sort=corr.columns, title=""),
    y=alt.Y("Variable1:N", sort=corr.columns, title=""),
    color=alt.Color("Correlation:Q", scale=alt.Scale(scheme='spectral', domain=(-1, 1))),
    tooltip=[
        alt.Tooltip('Variable1:N', title='Atributo 1'),
        alt.Tooltip('Variable2:N', title='Atributo 2'),
        alt.Tooltip('Correlation:Q', title='Correlação de Pearson', format='.2f'),

        alt.Tooltip('Aleatoriedade (r)_x:Q', title="Fator de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Aleatoriedade (r)_y:Q', title="Fator de Aleatoriedade (2)", format='.3f'),

        alt.Tooltip('Entropia_x:Q', title="Entropia de Shannon (1)", format='.3f'),
        alt.Tooltip('Entropia_y:Q', title="Entropia de Shannon (2)", format='.3f'),

        alt.Tooltip('Score_x:Q', title="Score de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Score_y:Q', title="Score de Aleatoriedade (2)", format='.3f'),
    ]
)

corr = base.mark_rect()

text = base.mark_text(baseline="middle").encode(
    text=alt.Text("Correlation:Q", format='.2f'),
    color=alt.value("white")
)

(corr + text).properties(
    title=alt.Title(
        text="Correlograma entre os atributos considerados 'Bem-Comportados'",
        subtitle=f"Atualmente existem {df2.shape[1]} atributos na análise"
    ),
    width=700,
    height=300
)

alt.LayerChart(...)

In [ ]:
#@title Seleção de Atributos pela Correlação e pelo Score de Aleatoriedade
metadata = corr_matrix[['Variable1', 'Variable2', 'Score_x', 'Score_y', 'Correlation']]

# Remove pares com a mesma variável
metadata = metadata[metadata.eval("Variable1 != Variable2")]

features = metadata['Variable1'].unique()

best_features = []

for feature in features:
  d = metadata[metadata['Variable1'] == feature]

  # Procura atributos altamente correlacionados com o atributo atual
  d = d[d['Correlation'] > 0.7]

  if d.shape[0] == 0:
    # Caso não houver nenhum atributo
    # correlacionado com o atributo atual, seleciona ele.
    best_features.append(feature)

  if d.shape[0] > 1:
    # Caso houver outros atributos altamente
    # correlacionados com o atual, escolhe o menos aleatório

    # Procura o nome e score da variável
    # correlacionada com menor score de aleatoriedade
    var_name, var_score = d.loc[d['Score_y'].idxmin(), ['Variable2', 'Score_y']].tolist()

    # Procura o score de aleatoriedade da variável atual
    current_score = d['Score_x'].min()

    # Seleciona a variável menos aleatória
    if current_score <= var_score:
      best_features.append(feature)
    else:
      best_features.append(var_name)


In [ ]:
#@title Correlograma dos Atributos Bem Comportados e Pouco Correlacionados

# Define o DataFrame com Atributos Comportados e Poucos Correlacionados
df3 = df2[list(set(best_features))]

# Filtra apenas os valores do triângulo inferior sem a diagonal principal
corr = df3.corr()
corr = corr.where(np.tril(np.ones(corr.shape), k=0).astype(bool))

# Calcula a matriz de correlação
corr_matrix = corr.reset_index().melt(id_vars='index', var_name='Variable2', value_name='Correlation')

# Renomeia a coluna 'index' para 'Variable1' para melhor compreensão
corr_matrix = corr_matrix.rename(columns={'index': 'Variable1'})

corr_matrix = corr_matrix.dropna()

# Adicionar métricas de aleatoriedade
corr_matrix = corr_matrix.merge(metrics, left_on="Variable1", right_on="Coluna", how="inner")
corr_matrix = corr_matrix.merge(metrics, left_on="Variable2", right_on="Coluna", how="inner")

base = alt.Chart(corr_matrix).encode(
    x=alt.X("Variable2:N", sort=corr.columns, title=""),
    y=alt.Y("Variable1:N", sort=corr.columns, title=""),
    color=alt.Color("Correlation:Q", scale=alt.Scale(scheme='spectral', domain=(-1, 1))),
    tooltip=[
        alt.Tooltip('Variable1:N', title='Atributo 1'),
        alt.Tooltip('Variable2:N', title='Atributo 2'),
        alt.Tooltip('Correlation:Q', title='Correlação de Pearson', format='.2f'),

        alt.Tooltip('Aleatoriedade (r)_x:Q', title="Fator de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Aleatoriedade (r)_y:Q', title="Fator de Aleatoriedade (2)", format='.3f'),

        alt.Tooltip('Entropia_x:Q', title="Entropia de Shannon (1)", format='.3f'),
        alt.Tooltip('Entropia_y:Q', title="Entropia de Shannon (2)", format='.3f'),

        alt.Tooltip('Score_x:Q', title="Score de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Score_y:Q', title="Score de Aleatoriedade (2)", format='.3f'),
    ]
)

corr = base.mark_rect()

text = base.mark_text(baseline="middle").encode(
    text=alt.Text("Correlation:Q", format='.2f'),
    color=alt.value("white")
)

(corr + text).properties(
    title=alt.Title(
        text="Correlograma entre os atributos considerados 'Bem-Comportados' e Pouco Correlacionados",
        subtitle=f"Atualmente existem {df3.shape[1]} atributos na análise"
    ),    width=700,
    height=300
)

alt.LayerChart(...)

In [ ]:
#@title Modelo de Regressão Linear Ajustada a Cada Dataset
from sklearn.linear_model import LinearRegression

y = level.copy()

results = [
    {"Dataset": "Original", "Variáveis": df.shape[1], "R2": LinearRegression().fit(df, y).score(df, y)},
    {"Dataset": "Bem Comportados",  "Variáveis": df2.shape[1],"R2": LinearRegression().fit(df2, y).score(df2, y)},
    {"Dataset": "Bem Comportados e Pouco Correlacionados", "Variáveis": df3.shape[1],"R2": LinearRegression().fit(df3, y).score(df3, y)}
]

pd.DataFrame(results)

Dataset  Variáveis        R2
0                                 Original         14  0.219404
1                          Bem Comportados         14  0.219404
2  Bem Comportados e Pouco Correlacionados          7  0.130100

# Dimensão Meio Ambiente

In [ ]:
df = MA

In [ ]:
#@title Relações entre os Atributos
metafeatures = compute_metafeatures(df, level)
X = pd.concat(metafeatures, axis=1)

columns_order = sort_columns_kmeans(metafeatures=X)

multi_scatter_1d(df[columns_order], level)

In [ ]:
#@title Calcular Métricas de Aleatoriedade para as Colunas do DataFrame
metrics = []

for idx, column in enumerate(columns_order):
  A = df.loc[:, column].to_numpy()

  # Fator de Aleatoriedade Corrigido do Vetor
  r_h, (x, zx, u) = compute_randomness(A)

  # Entropia de Shannon do Vetor
  e = compute_entropy(A)

  # Divergência de KL entre Vetor e Vetor-Alvo
  k = compute_entropy(A, level)

  metrics.append((f"({idx}) {column}", column, x, zx, u, r_h, e, k))

metrics = pd.DataFrame(metrics, columns=['Nome', 'Coluna', 'Tamanho (bytes)', 'Tamanho Zip (Bytes)',
                                         '% Valores Unicos', 'Aleatoriedade (r)', 'Entropia', 'KL'])

metrics.loc[metrics['Aleatoriedade (r)'] < 0, "Aleatoriedade (r)"] = 0

metrics.head(5)

Nome  \
0  (0) Soluções inteligentes para gestão na distr...   
1  (1) Percentual de material recolhido pela cole...   
2  (2) Soluções inteligentes para otimização da c...   
3  (3) Soluções em monitoramento de gases de efei...   
4               (4) Monitoramento da qualidade do ar   

                                              Coluna  Tamanho (bytes)  \
0  Soluções inteligentes para gestão na distribui...            44560   
1  Percentual de material recolhido pela coleta s...            44560   
2  Soluções inteligentes para otimização da colet...            44560   
3  Soluções em monitoramento de gases de efeito e...            44560   
4                   Monitoramento da qualidade do ar            44560   

   Tamanho Zip (Bytes)  % Valores Unicos  Aleatoriedade (r)  Entropia  \
0                   96          0.000718           0.067271  0.009527   
1                 2640          0.071813           0.000000  0.677232   
2                  121          0.000718           0.067832  0.018634   
3                   87          0.000718           0.067069  0.005184   
4                  104          0.000718           0.067451  0.011006   

         KL  
0  3.754514  
1  3.495629  
2  3.751728  
3  3.756752  
4  3.747732

In [ ]:
#@title Relação entre Entropia de Shannon e Fator de Aleatoriedade

# Calcula a correlação entre Fator de Aleatoriedade e Entropia
corr = metrics[['Aleatoriedade (r)', 'Entropia']].corr(method="spearman").iloc[0,1]

# Limites do retângulo
x_min, x_max = 0, 0.15
y_min, y_max = 0, 3

# Adiciona uma coluna para indicar se o ponto está dentro do retângulo
metrics['Comportamento'] = metrics.apply(
    lambda row: 'Bem Comportado' if (x_min <= row['Aleatoriedade (r)'] <= x_max and y_min <= row['Entropia'] <= y_max) else 'Mal Comportado',
    axis=1
)

# Calcula o Score de Aleatoriedade dos Atributos (Média entre Entropia e Fator de Aleatoriedade)
metrics['Score'] = (metrics['Aleatoriedade (r)'] + metrics['Entropia']) / 2

points = alt.Chart(metrics).mark_point().encode(
    x=alt.X("Aleatoriedade (r)", title="Fator de Aleatoriedade"),
    y=alt.Y("Entropia", title="Entropia de Shannon"),
    color=alt.Color("Comportamento:N",
                    scale=alt.Scale(domain=['Bem Comportado', 'Mal Comportado'], range=['blue', 'red']),
                    legend=alt.Legend(title="Comportamento do Atributo")),
    tooltip=[
        alt.Tooltip("Nome", title="Coluna"),
        alt.Tooltip("Aleatoriedade (r)", title="Fator de Aleatoriedade", format=".3f"),
        alt.Tooltip("Entropia", title="Entropia de Shannon", format=".3f"),
        alt.Tooltip("Score", title="Score de Aleatoriedade", format=".3f"),
    ]
)

rect = alt.Chart(pd.DataFrame({
    'x': [x_max], 'x2': [x_min],
    'y': [y_max], 'y2': [y_min]
})).mark_rect(opacity=0.3).encode(
    x='x:Q', x2='x2:Q',
    y='y:Q', y2='y2:Q',
    color=alt.value("grey")
)

good_zone = metrics[metrics['Comportamento'] == "Bem Comportado"]

good_points = alt.Chart(good_zone).mark_point().encode(
    x=alt.X("Aleatoriedade (r)", title="Fator de Aleatoriedade"),
    y=alt.Y("Entropia", title=""),
    color=alt.Color("Comportamento:N",
                    scale=alt.Scale(domain=['Bem Comportado', 'Mal Comportado'], range=['blue', 'red']),
                    legend=alt.Legend(title="Comportamento do Atributo")),
    tooltip=[
        alt.Tooltip("Nome", title="Coluna"),
        alt.Tooltip("Aleatoriedade (r)", title="Fator de Aleatoriedade", format=".3f"),
        alt.Tooltip("Entropia", title="Entropia de Shannon", format=".3f"),
        alt.Tooltip("Score", title="Score de Aleatoriedade", format=".3f"),
    ]
).properties(
    title=alt.Title(
        text="Atributos Dentro da Zona Bem Comportada",
        subtitle=f"Existem {good_zone.shape[0]} atributos bem comportados nessa zona",
        anchor="start",     # Alinha o título ao início (canto esquerdo)
        align="left",       # Alinha o texto à esquerda
    ),
)

plot = (rect + points).properties(
    title=alt.Title(
        text="Relação entre Entropia de Shannon e Fator de Aleatoriedade",
        subtitle=f"A Correlação de Spearman entre o Fator de Aleatoriedade e a Entropia de Shannon é de {corr:.4f}",
        anchor="start",     # Alinha o título ao início (canto esquerdo)
        align="left",       # Alinha o texto à esquerda
    ),
    width=500,
    height=300,
)

(plot | good_points).properties(
    padding={"left": 25, "right": 25, "top": 25, "bottom": 25}  # Adiciona padding externo
).interactive()

alt.HConcatChart(...)

In [ ]:
#@title Análise dos Atributos Bem Comportados
good_columns = metrics[metrics['Comportamento'] == "Bem Comportado"]['Coluna'].tolist()

# Define o DataFrame com apenas os atributos comportados
df2 = df[good_columns].copy()

metafeatures = compute_metafeatures(df2, level)
X = pd.concat(metafeatures, axis=1)

columns_order_hat = sort_columns_kmeans(metafeatures=X)

multi_scatter_1d(df2[columns_order_hat], level)

In [ ]:
#@title Correlograma dos Atributos Bem Comportados

# Filtra apenas os valores do triângulo inferior sem a diagonal principal
corr = df2.corr()
corr = corr.where(np.tril(np.ones(corr.shape), k=0).astype(bool))

# Calcula a matriz de correlação
corr_matrix = corr.reset_index().melt(id_vars='index', var_name='Variable2', value_name='Correlation')

# Renomeia a coluna 'index' para 'Variable1' para melhor compreensão
corr_matrix = corr_matrix.rename(columns={'index': 'Variable1'})

corr_matrix = corr_matrix.dropna()

# Adicionar métricas de aleatoriedade
corr_matrix = corr_matrix.merge(metrics, left_on="Variable1", right_on="Coluna", how="inner")
corr_matrix = corr_matrix.merge(metrics, left_on="Variable2", right_on="Coluna", how="inner")

base = alt.Chart(corr_matrix).encode(
    x=alt.X("Variable2:N", sort=corr.columns, title=""),
    y=alt.Y("Variable1:N", sort=corr.columns, title=""),
    color=alt.Color("Correlation:Q", scale=alt.Scale(scheme='spectral', domain=(-1, 1))),
    tooltip=[
        alt.Tooltip('Variable1:N', title='Atributo 1'),
        alt.Tooltip('Variable2:N', title='Atributo 2'),
        alt.Tooltip('Correlation:Q', title='Correlação de Pearson', format='.2f'),

        alt.Tooltip('Aleatoriedade (r)_x:Q', title="Fator de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Aleatoriedade (r)_y:Q', title="Fator de Aleatoriedade (2)", format='.3f'),

        alt.Tooltip('Entropia_x:Q', title="Entropia de Shannon (1)", format='.3f'),
        alt.Tooltip('Entropia_y:Q', title="Entropia de Shannon (2)", format='.3f'),

        alt.Tooltip('Score_x:Q', title="Score de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Score_y:Q', title="Score de Aleatoriedade (2)", format='.3f'),
    ]
)

corr = base.mark_rect()

text = base.mark_text(baseline="middle").encode(
    text=alt.Text("Correlation:Q", format='.2f'),
    color=alt.value("white")
)

(corr + text).properties(
    title="Correlograma entre os atributos considerados 'Bem-Comportados'",
    width=700,
    height=300
)

alt.LayerChart(...)

In [ ]:
#@title Seleção de Atributos pela Correlação e pelo Score de Aleatoriedade
metadata = corr_matrix[['Variable1', 'Variable2', 'Score_x', 'Score_y', 'Correlation']]

# Remove pares com a mesma variável
metadata = metadata[metadata.eval("Variable1 != Variable2")]

features = metadata['Variable1'].unique()

best_features = []

for feature in features:
  d = metadata[metadata['Variable1'] == feature]

  # Procura atributos altamente correlacionados com o atributo atual
  d = d[d['Correlation'] > 0.7]

  if d.shape[0] == 0:
    # Caso não houver nenhum atributo
    # correlacionado com o atributo atual, seleciona ele.
    best_features.append(feature)

  if d.shape[0] > 1:
    # Caso houver outros atributos altamente
    # correlacionados com o atual, escolhe o menos aleatório

    # Procura o nome e score da variável
    # correlacionada com menor score de aleatoriedade
    var_name, var_score = d.loc[d['Score_y'].idxmin(), ['Variable2', 'Score_y']].tolist()

    # Procura o score de aleatoriedade da variável atual
    current_score = d['Score_x'].min()

    # Seleciona a variável menos aleatória
    if current_score <= var_score:
      best_features.append(feature)
    else:
      best_features.append(var_name)


In [ ]:
#@title Correlograma dos Atributos Bem Comportados e Pouco Correlacionados

# Filtra apenas os valores do triângulo inferior sem a diagonal principal
corr = df2[list(set(best_features))].corr()
corr = corr.where(np.tril(np.ones(corr.shape), k=0).astype(bool))

# Calcula a matriz de correlação
corr_matrix = corr.reset_index().melt(id_vars='index', var_name='Variable2', value_name='Correlation')

# Renomeia a coluna 'index' para 'Variable1' para melhor compreensão
corr_matrix = corr_matrix.rename(columns={'index': 'Variable1'})

corr_matrix = corr_matrix.dropna()

# Adicionar métricas de aleatoriedade
corr_matrix = corr_matrix.merge(metrics, left_on="Variable1", right_on="Coluna", how="inner")
corr_matrix = corr_matrix.merge(metrics, left_on="Variable2", right_on="Coluna", how="inner")

base = alt.Chart(corr_matrix).encode(
    x=alt.X("Variable2:N", sort=corr.columns, title=""),
    y=alt.Y("Variable1:N", sort=corr.columns, title=""),
    color=alt.Color("Correlation:Q", scale=alt.Scale(scheme='spectral', domain=(-1, 1))),
    tooltip=[
        alt.Tooltip('Variable1:N', title='Atributo 1'),
        alt.Tooltip('Variable2:N', title='Atributo 2'),
        alt.Tooltip('Correlation:Q', title='Correlação de Pearson', format='.2f'),

        alt.Tooltip('Aleatoriedade (r)_x:Q', title="Fator de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Aleatoriedade (r)_y:Q', title="Fator de Aleatoriedade (2)", format='.3f'),

        alt.Tooltip('Entropia_x:Q', title="Entropia de Shannon (1)", format='.3f'),
        alt.Tooltip('Entropia_y:Q', title="Entropia de Shannon (2)", format='.3f'),

        alt.Tooltip('Score_x:Q', title="Score de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Score_y:Q', title="Score de Aleatoriedade (2)", format='.3f'),
    ]
)

corr = base.mark_rect()

text = base.mark_text(baseline="middle").encode(
    text=alt.Text("Correlation:Q", format='.2f'),
    color=alt.value("white")
)

(corr + text).properties(
    title="Correlograma entre os atributos considerados 'Bem-Comportados' e Pouco Correlacionados",
    width=700,
    height=300
)

alt.LayerChart(...)

In [ ]:
#@title Atributos Bem Comportados e Pouco Correlacionados

# Define o DataFrame com Atributos Comportados e Poucos Correlacionados
df3 = df2[list(set(best_features))]

df3.shape

(5570, 5)

In [ ]:
#@title Modelo de Regressão Linear Ajustada a Cada Dataset
from sklearn.linear_model import LinearRegression

y = level.copy()

results = [
    {"Dataset": "Original", "Variáveis": df.shape[1], "R2": LinearRegression().fit(df, y).score(df, y)},
    {"Dataset": "Bem Comportados",  "Variáveis": df2.shape[1],"R2": LinearRegression().fit(df2, y).score(df2, y)},
    {"Dataset": "Bem Comportados e Pouco Correlacionados", "Variáveis": df3.shape[1],"R2": LinearRegression().fit(df3, y).score(df3, y)}
]

pd.DataFrame(results)

Dataset  Variáveis        R2
0                                 Original         12  0.377683
1                          Bem Comportados          9  0.276615
2  Bem Comportados e Pouco Correlacionados          5  0.275264

# Dimensão Sociocultural

In [ ]:
df = SC

In [ ]:
#@title Relações entre os Atributos
metafeatures = compute_metafeatures(df, level)
X = pd.concat(metafeatures, axis=1)

columns_order = sort_columns_kmeans(metafeatures=X)

multi_scatter_1d(df[columns_order], level)

In [ ]:
#@title Calcular Métricas de Aleatoriedade para as Colunas do DataFrame
metrics = []

for idx, column in enumerate(columns_order):
  A = df.loc[:, column].to_numpy()

  # Fator de Aleatoriedade Corrigido do Vetor
  r_h, (x, zx, u) = compute_randomness(A)

  # Entropia de Shannon do Vetor
  e = compute_entropy(A)

  # Divergência de KL entre Vetor e Vetor-Alvo
  k = compute_entropy(A, level)

  metrics.append((f"({idx}) {column}", column, x, zx, u, r_h, e, k))

metrics = pd.DataFrame(metrics, columns=['Nome', 'Coluna', 'Tamanho (bytes)', 'Tamanho Zip (Bytes)',
                                         '% Valores Unicos', 'Aleatoriedade (r)', 'Entropia', 'KL'])

metrics.loc[metrics['Aleatoriedade (r)'] < 0, "Aleatoriedade (r)"] = 0

metrics.head(5)

Nome  \
0  (0) Médicos disponíveis na rede pública municipal   
1        (1) Inclusão social para grupos específicos   
2               (2) Políticas públicas para mulheres   
3                             (3) Taxa de homicídios   
4  (4) Soluções em monitoramento para a segurança...   

                                              Coluna  Tamanho (bytes)  \
0      Médicos disponíveis na rede pública municipal            44560   
1            Inclusão social para grupos específicos            44560   
2                   Políticas públicas para mulheres            44560   
3                                 Taxa de homicídios            44560   
4  Soluções em monitoramento para a segurança púb...            44560   

   Tamanho Zip (Bytes)  % Valores Unicos  Aleatoriedade (r)  Entropia  \
0                10331          0.111849           0.074679  4.044764   
1                 3733          0.002693           0.125550  1.835994   
2                 2098          0.001616           0.101260  0.900025   
3                13429          0.505386           0.083184  4.201449   
4                  149          0.001077           0.064017  0.029865   

         KL  
0  4.743997  
1  5.123780  
2  3.716288  
3  3.114306  
4  3.747118

In [ ]:
#@title Relação entre Entropia de Shannon e Fator de Aleatoriedade

# Calcula a correlação entre Fator de Aleatoriedade e Entropia
corr = metrics[['Aleatoriedade (r)', 'Entropia']].corr(method="spearman").iloc[0,1]

# Limites do retângulo
x_min, x_max = 0, 0.18
y_min, y_max = 0, 3

# Adiciona uma coluna para indicar se o ponto está dentro do retângulo
metrics['Comportamento'] = metrics.apply(
    lambda row: 'Bem Comportado' if (x_min <= row['Aleatoriedade (r)'] <= x_max and y_min <= row['Entropia'] <= y_max) else 'Mal Comportado',
    axis=1
)

# Calcula o Score de Aleatoriedade dos Atributos (Média entre Entropia e Fator de Aleatoriedade)
metrics['Score'] = (metrics['Aleatoriedade (r)'] + metrics['Entropia']) / 2

points = alt.Chart(metrics).mark_point().encode(
    x=alt.X("Aleatoriedade (r)", title="Fator de Aleatoriedade"),
    y=alt.Y("Entropia", title="Entropia de Shannon"),
    color=alt.Color("Comportamento:N",
                    scale=alt.Scale(domain=['Bem Comportado', 'Mal Comportado'], range=['blue', 'red']),
                    legend=alt.Legend(title="Comportamento do Atributo")),
    tooltip=[
        alt.Tooltip("Nome", title="Coluna"),
        alt.Tooltip("Aleatoriedade (r)", title="Fator de Aleatoriedade", format=".3f"),
        alt.Tooltip("Entropia", title="Entropia de Shannon", format=".3f"),
        alt.Tooltip("Score", title="Score de Aleatoriedade", format=".3f"),
    ]
)

rect = alt.Chart(pd.DataFrame({
    'x': [x_max], 'x2': [x_min],
    'y': [y_max], 'y2': [y_min]
})).mark_rect(opacity=0.3).encode(
    x='x:Q', x2='x2:Q',
    y='y:Q', y2='y2:Q',
    color=alt.value("grey")
)

good_zone = metrics[metrics['Comportamento'] == "Bem Comportado"]

good_points = alt.Chart(good_zone).mark_point().encode(
    x=alt.X("Aleatoriedade (r)", title="Fator de Aleatoriedade"),
    y=alt.Y("Entropia", title=""),
    color=alt.Color("Comportamento:N",
                    scale=alt.Scale(domain=['Bem Comportado', 'Mal Comportado'], range=['blue', 'red']),
                    legend=alt.Legend(title="Comportamento do Atributo")),
    tooltip=[
        alt.Tooltip("Nome", title="Coluna"),
        alt.Tooltip("Aleatoriedade (r)", title="Fator de Aleatoriedade", format=".3f"),
        alt.Tooltip("Entropia", title="Entropia de Shannon", format=".3f"),
        alt.Tooltip("Score", title="Score de Aleatoriedade", format=".3f"),
    ]
).properties(
    title=alt.Title(
        text="Atributos Dentro da Zona Bem Comportada",
        subtitle=f"Existem {good_zone.shape[0]} atributos bem comportados nessa zona",
        anchor="start",     # Alinha o título ao início (canto esquerdo)
        align="left",       # Alinha o texto à esquerda
    ),
)

plot = (rect + points).properties(
    title=alt.Title(
        text="Relação entre Entropia de Shannon e Fator de Aleatoriedade",
        subtitle=f"A Correlação de Spearman entre o Fator de Aleatoriedade e a Entropia de Shannon é de {corr:.4f}",
        anchor="start",     # Alinha o título ao início (canto esquerdo)
        align="left",       # Alinha o texto à esquerda
    ),
    width=500,
    height=300,
)

(plot | good_points).properties(
    padding={"left": 25, "right": 25, "top": 25, "bottom": 25}  # Adiciona padding externo
).interactive()

alt.HConcatChart(...)

In [ ]:
#@title Análise dos Atributos Bem Comportados
good_columns = metrics[metrics['Comportamento'] == "Bem Comportado"]['Coluna'].tolist()

# Define o DataFrame com apenas os atributos comportados
df2 = df[good_columns].copy()

metafeatures = compute_metafeatures(df2, level)
X = pd.concat(metafeatures, axis=1)

columns_order_hat = sort_columns_kmeans(metafeatures=X)

multi_scatter_1d(df2[columns_order_hat], level)

In [ ]:
#@title Correlograma dos Atributos Bem Comportados

# Filtra apenas os valores do triângulo inferior sem a diagonal principal
corr = df2.corr()
corr = corr.where(np.tril(np.ones(corr.shape), k=0).astype(bool))

# Calcula a matriz de correlação
corr_matrix = corr.reset_index().melt(id_vars='index', var_name='Variable2', value_name='Correlation')

# Renomeia a coluna 'index' para 'Variable1' para melhor compreensão
corr_matrix = corr_matrix.rename(columns={'index': 'Variable1'})

corr_matrix = corr_matrix.dropna()

# Adicionar métricas de aleatoriedade
corr_matrix = corr_matrix.merge(metrics, left_on="Variable1", right_on="Coluna", how="inner")
corr_matrix = corr_matrix.merge(metrics, left_on="Variable2", right_on="Coluna", how="inner")

base = alt.Chart(corr_matrix).encode(
    x=alt.X("Variable2:N", sort=corr.columns, title=""),
    y=alt.Y("Variable1:N", sort=corr.columns, title=""),
    color=alt.Color("Correlation:Q", scale=alt.Scale(scheme='spectral', domain=(-1, 1))),
    tooltip=[
        alt.Tooltip('Variable1:N', title='Atributo 1'),
        alt.Tooltip('Variable2:N', title='Atributo 2'),
        alt.Tooltip('Correlation:Q', title='Correlação de Pearson', format='.2f'),

        alt.Tooltip('Aleatoriedade (r)_x:Q', title="Fator de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Aleatoriedade (r)_y:Q', title="Fator de Aleatoriedade (2)", format='.3f'),

        alt.Tooltip('Entropia_x:Q', title="Entropia de Shannon (1)", format='.3f'),
        alt.Tooltip('Entropia_y:Q', title="Entropia de Shannon (2)", format='.3f'),

        alt.Tooltip('Score_x:Q', title="Score de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Score_y:Q', title="Score de Aleatoriedade (2)", format='.3f'),
    ]
)

corr = base.mark_rect()

text = base.mark_text(baseline="middle").encode(
    text=alt.Text("Correlation:Q", format='.2f'),
    color=alt.value("white")
)

(corr + text).properties(
    title="Correlograma entre os atributos considerados 'Bem-Comportados'",
    width=700,
    height=300
)

alt.LayerChart(...)

In [ ]:
#@title Seleção de Atributos pela Correlação e pelo Score de Aleatoriedade
metadata = corr_matrix[['Variable1', 'Variable2', 'Score_x', 'Score_y', 'Correlation']]

# Remove pares com a mesma variável
metadata = metadata[metadata.eval("Variable1 != Variable2")]

features = metadata['Variable1'].unique()

best_features = []

for feature in features:
  d = metadata[metadata['Variable1'] == feature]

  # Procura atributos altamente correlacionados com o atributo atual
  d = d[d['Correlation'] > 0.7]

  if d.shape[0] == 0:
    # Caso não houver nenhum atributo
    # correlacionado com o atributo atual, seleciona ele.
    best_features.append(feature)

  if d.shape[0] > 1:
    # Caso houver outros atributos altamente
    # correlacionados com o atual, escolhe o menos aleatório

    # Procura o nome e score da variável
    # correlacionada com menor score de aleatoriedade
    var_name, var_score = d.loc[d['Score_y'].idxmin(), ['Variable2', 'Score_y']].tolist()

    # Procura o score de aleatoriedade da variável atual
    current_score = d['Score_x'].min()

    # Seleciona a variável menos aleatória
    if current_score <= var_score:
      best_features.append(feature)
    else:
      best_features.append(var_name)


In [ ]:
#@title Correlograma dos Atributos Bem Comportados e Pouco Correlacionados

# Filtra apenas os valores do triângulo inferior sem a diagonal principal
corr = df2[list(set(best_features))].corr()
corr = corr.where(np.tril(np.ones(corr.shape), k=0).astype(bool))

# Calcula a matriz de correlação
corr_matrix = corr.reset_index().melt(id_vars='index', var_name='Variable2', value_name='Correlation')

# Renomeia a coluna 'index' para 'Variable1' para melhor compreensão
corr_matrix = corr_matrix.rename(columns={'index': 'Variable1'})

corr_matrix = corr_matrix.dropna()

# Adicionar métricas de aleatoriedade
corr_matrix = corr_matrix.merge(metrics, left_on="Variable1", right_on="Coluna", how="inner")
corr_matrix = corr_matrix.merge(metrics, left_on="Variable2", right_on="Coluna", how="inner")

base = alt.Chart(corr_matrix).encode(
    x=alt.X("Variable2:N", sort=corr.columns, title=""),
    y=alt.Y("Variable1:N", sort=corr.columns, title=""),
    color=alt.Color("Correlation:Q", scale=alt.Scale(scheme='spectral', domain=(-1, 1))),
    tooltip=[
        alt.Tooltip('Variable1:N', title='Atributo 1'),
        alt.Tooltip('Variable2:N', title='Atributo 2'),
        alt.Tooltip('Correlation:Q', title='Correlação de Pearson', format='.2f'),

        alt.Tooltip('Aleatoriedade (r)_x:Q', title="Fator de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Aleatoriedade (r)_y:Q', title="Fator de Aleatoriedade (2)", format='.3f'),

        alt.Tooltip('Entropia_x:Q', title="Entropia de Shannon (1)", format='.3f'),
        alt.Tooltip('Entropia_y:Q', title="Entropia de Shannon (2)", format='.3f'),

        alt.Tooltip('Score_x:Q', title="Score de Aleatoriedade (1)", format='.3f'),
        alt.Tooltip('Score_y:Q', title="Score de Aleatoriedade (2)", format='.3f'),
    ]
)

corr = base.mark_rect()

text = base.mark_text(baseline="middle").encode(
    text=alt.Text("Correlation:Q", format='.2f'),
    color=alt.value("white")
)

(corr + text).properties(
    title="Correlograma entre os atributos considerados 'Bem-Comportados' e Pouco Correlacionados",
    width=700,
    height=300
)

alt.LayerChart(...)

In [ ]:
#@title Atributos Bem Comportados e Pouco Correlacionados

# Define o DataFrame com Atributos Comportados e Poucos Correlacionados
df3 = df2[list(set(best_features))]

df3.shape

(5570, 17)

In [ ]:
#@title Modelo de Regressão Linear Ajustada a Cada Dataset
from sklearn.linear_model import LinearRegression

y = level.copy()

results = [
    {"Dataset": "Original", "Variáveis": df.shape[1], "R2": LinearRegression().fit(df, y).score(df, y)},
    {"Dataset": "Bem Comportados",  "Variáveis": df2.shape[1],"R2": LinearRegression().fit(df2, y).score(df2, y)},
    {"Dataset": "Bem Comportados e Pouco Correlacionados", "Variáveis": df3.shape[1],"R2": LinearRegression().fit(df3, y).score(df3, y)}
]

pd.DataFrame(results)

Dataset  Variáveis        R2
0                                 Original         31  0.455643
1                          Bem Comportados         23  0.405783
2  Bem Comportados e Pouco Correlacionados         17  0.405532


- Estudar comportamento das variáveis mal-comportadas
- Calcular correlações entre variaveis mal-comportadas e realizar seleção de features entre elas
- Usar features mal-comportadas selecionadas para melhorar os modelos Bem-comportados e Bem-comportados e Poucos Correlacionados
- Usar modelos não-lineares para verificar a qualidade das features selecionadas
- Plotar gráfico do número de features pela qualidade do modelo
- Usar validação cruzada para testar modelos